## 라이브러리 불러오기

In [3]:
# API 호출
# ## https://data.go.kr/tcs/dss/selectApiDataDetailView.do?publicDataPk=15057440
from urllib.request import Request, urlopen
# Request https://docs.python.org/ko/3/library/urllib.request.html#urllib.request.Request
# urlopen https://docs.python.org/ko/3/library/urllib.request.html#urllib.request.urlopen
from urllib.parse import urlencode, quote_plus
# urlenocde https://docs.python.org/ko/3/library/urllib.parse.html#urllib.parse.urlencode
# quote_plus https://docs.python.org/ko/3/library/urllib.parse.html#urllib.parse.quote_plus
from urllib.parse import unquote
import requests

# 시간 생성
import time
import datetime
from pytz import timezone, utc

# 폴더 자동 생성
import os

# 코드 스케줄링
import threading
# import schedule

# XML 파싱
import xml.etree.ElementTree as ET

# 입력데이터 데이터프레임 작성
import pandas as pd
import numpy as np

# DataFrame 화면 출력                                                # DataFrame 화면 출력 설정이 변경되어 있습니다 #
from IPython.display import display
pd.options.display.max_columns = None
pd.options.display.max_rows = None # default = 60


In [52]:
# 폴더 자동 생성 함수
# https://data-make.tistory.com/170
def createFolder(directory):
    try:
        if not os.path.exists(directory):
            os.makedirs(directory)
    except OSError:
        print ('Error: Creating directory. ' +  directory)

## 기본값 설정하기

In [3]:
routeId = 229000266
year = 2020
month = 11
day = 18

## Key Unquote

In [30]:
KEY = 'yEaR%2F3MDedRSlVJL%2F2pxnVg0yre1N5VF3RZ%2FUAt56MJ7J2mNpfqhUvy05pXV0uhHTVY7DbyCR8xmMaDdYga67Q%3D%3D' # 종현
apiKey = unquote(KEY)

## API 호출

In [31]:
# 노선정보항목조회 busrouteservice/info
# routeId의 정류장 목록을 받아옵니다.
url = 'http://openapi.gbis.go.kr/ws/rest/busrouteservice/station'
queryParams = '?' + urlencode({ quote_plus('serviceKey') : apiKey, quote_plus('routeId') : routeId })
request = Request(url + queryParams)
request.get_method = lambda: 'GET'

# API를 호출하여 XML 형식으로 된 string 데이터를 변수 "oneLineXML" 에 저장합니다.
oneLineXML = urlopen(request).read().decode('utf8')
# oneLineXML

## XML 파싱

In [34]:
# xtree는 "openapi" 도메인 API 호출에서 "headerCd"에 상관없이 3개의 태그를 갖습니다.
# [comMsgHeader, msgHeader, msgBody]
xtree = ET.fromstring(oneLineXML)
# for branch in xtree:
#     print(branch)
msgBody = xtree[2]

tagList = ["stationSeq", "stationId", "stationName"]
stationList = []
for branch in msgBody:
    stationList.append([branch.find(tag).text for tag in tagList])

# station_df의 index가 0부터 시작하는 문제를 해결 하기 위해 rangeIndex를 지정하였습니다.
stationCount = len(stationList) # 뒤에서 다시 사용되므로 함수로 선언시 주의
rangeIndex = pd.RangeIndex(start=1, stop=stationCount+1)

station_df = pd.DataFrame(stationList, columns=tagList, index=rangeIndex)
station_df = station_df.astype({
    "stationSeq" : "int32",
    "stationId" : "int32", 
    "stationName" : "string"
    
})
# station_df

## 데이터 불러오기

In [47]:
subCategoryDict = {'dtt' : '/daily-time-table/', 
                   'dtt-log' : '/log/daily-time-table/', 
                   'rid' : '/route-id-list/',
                   'main-log' : '/log/main/',
                   'info' : '/BusInfo/',
                   'dtt-output' : '/out/daily-time-table/'
                  }

In [50]:
root = os.getcwd()
subCategory = subCategoryDict['dtt-output']
routeId = 204000046
folderPath = root + '/AWS/DATA' + subCategory + str(routeId)
outputPath = folderPath + '/2020-11-25.txt'

In [ ]:
root = os.getcwd()
subCategory = subCategoryDict['dtt']
routeId = 204000046
inputPath = root + '/AWS/DATA' + subCategory + str(routeId) + '/2020-11-25.txt'

In [53]:
createFolder(folderPath)

In [41]:
itemTagList = ['endBus', 'lowPlate', 'plateNo', 'plateType', 'remainSeatCnt', 'routeId', 'stationId', 'stationSeq', 'Nan']
# itemTagList = ['endBus', 'plateNo', 'plateType', 'remainSeatCnt', 'routeId', 'stationId', 'stationSeq', 'Nan']
itemTagList.insert(0, 'DateTime')
_df = pd.read_csv(inputPath, sep=' ', skiprows=[0], names=itemTagList)
_df = _df.drop(["Nan"], axis=1)
_df = _df.sort_values(['plateNo'])
_df = _df.dropna()
# _df = _df.drop(_df[_df["endBus"]=="API"].index)

# string을 datetime객체로 변환하기
_df['DateTime'] = pd.to_datetime(_df['DateTime'])
# dateTimeObj = datetime.datetime.strptime(_df['DateTime'], '%Y-%m-%dT%H:%M:%S.%f%z')
# _df['DateTime'] = _df.DateTime.str.split('.').str[0]
# _df['DateTime'] = _df.DateTime.str.replace('T', ' ')

_df = _df.astype({
    'endBus': 'int32', 
    'lowPlate': 'int32', 
    'plateNo': 'string', 
    'plateType': 'int32',
    'remainSeatCnt': 'int32', 
    'routeId': 'int32', 
    'stationId': 'int32', 
    'stationSeq': 'int32'
})
_df

DateTime  endBus  lowPlate    plateNo  plateType  \
1012 2020-11-25 07:56:48.137704+09:00       0         0  강원71바1297          3   
1471 2020-11-25 08:33:50.686079+09:00       0         0  강원71바1297          3   
1566 2020-11-25 08:41:38.166263+09:00       0         0  강원71바1297          3   
1338 2020-11-25 08:23:07.453215+09:00       0         0  강원71바1297          3   
1238 2020-11-25 08:15:19.295487+09:00       0         0  강원71바1297          3   
1733 2020-11-25 08:56:14.084847+09:00       0         0  강원71바1297          3   
1755 2020-11-25 08:58:10.582751+09:00       0         0  강원71바1297          3   
933  2020-11-25 07:49:58.229257+09:00       0         0  강원71바1297          3   
1001 2020-11-25 07:55:49.802956+09:00       0         0  강원71바1297          3   
1641 2020-11-25 08:48:27.744126+09:00       0         0  강원71바1297          3   
1481 2020-11-25 08:34:48.729699+09:00       0         0  강원71바1297          3   
1112 2020-11-25 08:05:34.838091+09:00       0         0  강원71바1297          3   
1676 2020-11-25 08:51:22.605264+09:00       0         0  강원71바1297          3   
1385 2020-11-25 08:27:01.319625+09:00       0         0  강원71바1297          3   
1251 2020-11-25 08:16:18.264460+09:00       0         0  강원71바1297          3   
1597 2020-11-25 08:44:33.697761+09:00       0         0  강원71바1297          3   
1370 2020-11-25 08:26:03.165527+09:00       0         0  강원71바1297          3   
1264 2020-11-25 08:17:16.628575+09:00       0         0  강원71바1297          3   
1123 2020-11-25 08:06:33.192306+09:00       0         0  강원71바1297          3   
988  2020-11-25 07:54:50.678909+09:00       0         0  강원71바1297          3   
1432 2020-11-25 08:30:55.325220+09:00       0         0  강원71바1297          3   
1402 2020-11-25 08:27:59.573693+09:00       0         0  강원71바1297          3   
956  2020-11-25 07:51:54.593162+09:00       0         0  강원71바1297          3   
1652 2020-11-25 08:49:25.887393+09:00       0         0  강원71바1297          3   
1358 2020-11-25 08:25:04.171327+09:00       0         0  강원71바1297          3   
1744 2020-11-25 08:57:12.188774+09:00       0         0  강원71바1297          3   
1450 2020-11-25 08:31:53.879019+09:00       0         0  강원71바1297          3   
1588 2020-11-25 08:43:35.504004+09:00       0         0  강원71바1297          3   
966  2020-11-25 07:52:53.451083+09:00       0         0  강원71바1297          3   
1072 2020-11-25 08:01:41.040573+09:00       0         0  강원71바1297          3   
1554 2020-11-25 08:40:39.232351+09:00       0         0  강원71바1297          3   
1137 2020-11-25 08:07:32.256710+09:00       0         0  강원71바1297          3   
1220 2020-11-25 08:14:21.165983+09:00       0         0  강원71바1297          3   
1151 2020-11-25 08:08:30.701156+09:00       0         0  강원71바1297          3   
1575 2020-11-25 08:42:37.040131+09:00       0         0  강원71바1297          3   
1347 2020-11-25 08:24:06.037342+09:00       0         0  강원71바1297          3   
1460 2020-11-25 08:32:52.152540+09:00       0         0  강원71바1297          3   
1195 2020-11-25 08:12:24.567765+09:00       0         0  강원71바1297          3   
940  2020-11-25 07:50:56.433110+09:00       0         0  강원71바1297          3   
1664 2020-11-25 08:50:24.231254+09:00       0         0  강원71바1297          3   
971  2020-11-25 07:53:52.594947+09:00       0         0  강원71바1297          3   
1421 2020-11-25 08:29:56.651727+09:00       0         0  강원71바1297          3   
1208 2020-11-25 08:13:22.881990+09:00       0         0  강원71바1297          3   
1324 2020-11-25 08:22:08.549069+09:00       0         0  강원71바1297          3   
1175 2020-11-25 08:10:28.059516+09:00       0         0  강원71바1297          3   
1711 2020-11-25 08:54:17.236957+09:00       0         0  강원71바1297          3   
1094 2020-11-25 08:03:38.579639+09:00       0         0  강원71바1297          3   
1042 2020-11-25 07:59:44.141613+09:00       0         0  강원71바1297          3   
1545 2020-11-25 08:39:41.218725+09:00       0         0  강원7

In [115]:
# stationSeq 가 뒤바뀌는 사례도 발생합니다. 
# cf) routeId = 204000046, DateTime = 20-11-17, plateNo = 경기78아1147, index = 166
# _df[_df['plateNo']=='경기78아1178'].sort_values(by='DateTime').reset_index(drop=True).iloc[-60:] 

In [23]:
# 차량 운행기록을 "plateNo"를 기준으로 구분합니다.
plateNoList = _df.groupby(['plateNo']).size().index
plateNoList

Index(['강원71바1297', '경기70아6926', '경기70아7361', '경기70아7474', '경기70아7482',
       '경기70아8601', '경기70아8789', '경기70아8880', '경기76사5089', '경기77바1097',
       '경기77바1198', '경기78아1117', '경기78아1147', '경기78아1178'],
      dtype='object', name='plateNo')

In [116]:
# 차량 번호 한개에 대해서 검사를 실행합니다.
temp_df =_df[_df['plateNo']=='경기78아1178'].sort_values(by='DateTime').reset_index(drop=True)
tempIndexList = []
for i in range(1, len(temp_df)):
    if(temp_df.iloc[i-1]['stationSeq'] > temp_df.iloc[i]['stationSeq']):
            tempIndexList.append(i)
            # print((temp_df.iloc[i-1]['stationSeq'] , temp_df.iloc[i]['stationSeq']))
            # print(i)
            
    tempIndexList.append(len(temp_df))
# display(temp_df.iloc[-60:].groupby('stationSeq').min())

In [91]:
# 정류장의 수 만큼 행을 갖는 빈 데이터프레임을 생성합니다. 변수 rangeIndex는 [XML파싱]에서 선언되어 있습니다.
rangeIndex = pd.RangeIndex(start=1, stop=stationCount+1)
_oneDay_df = pd.DataFrame(index = rangeIndex)

In [109]:
# 각 차량 번호를 기준으로 반복문을 수행합니다.
for plateNo in plateNoList:
    
    # 특정 차량번호와 같은 운행기록을 "DateTime을 기준으로 오름차순으로 정렬합니다."
    sameBusList = _df[_df['plateNo'] == plateNo].sort_values(['DateTime']).reset_index(drop=True)
#     display(sameBusList)
    
    
    # 버스는 뒤로가지 않으므로
    # "stationSeq"가 작아지는 인덱스 i의 리스트를 만듭니다.
    # API 호출 오류로 stationSeq가 작아지는 경우가 있습니다. 이 문제를 해결하기 위해 보정계수 diffK를 둡니다. 
    indexList = []
    diffK = 10 if ( True ) else 0
    for i in range(1,len(sameBusList)):
        if(sameBusList.iloc[i-1]['stationSeq'] > sameBusList.iloc[i]['stationSeq'] + diffK ):
            indexList.append(i)
#             print((sameBusList.iloc[i-1]['stationSeq'] , sameBusList.iloc[i]['stationSeq']))
            
    indexList.append(len(sameBusList))
    # print(indexList)
    
    # 첫번재 인덱스, 인덱스의 리스트, 마지막 인덱스를 조합하여 호차별로 운행기록을 구분합니다.
    index = 0
    tupleList = []
    for i in indexList:
        tupleList.append((index, i))
        small_df = sameBusList.iloc[index:i].groupby(by=['stationSeq']).min()
        # display(small_df)
        
        # 정류소 데이터프레임에 합칩니다.
        merge_df = pd.merge(station_df, small_df, how='outer',  left_index=True, right_index=True)        ###### ERROR 발생 히스토리 지점 by='stationSeq' 로 했을때 index가 0부터 시작
        # merge_df = merge_df.set_index(keys='stationSeq')
        
        if(0):
            # 1번 정류장에 대한 DateTime의 결측치가 많으면 1일 시간표에서 column 전체가 정렬이 안되므로 bfill방식으로 두번 결측치를 채웁니다.
            merge_df['DateTime'] = merge_df['DateTime'].interpolate(method='bfill', limit=1)
#             merge_df['DateTime'] = merge_df['DateTime'].interpolate(method='ffill', limit=1)
#             merge_df['DateTime'] = merge_df['DateTime'].interpolate(method='bfill', limit=1)


        if(0):
            # 결측치를 채울 경우 문제가 되는 데이터가 잘 드러나지 않으므로 결측치는 가장 마지막에 채우세요.
            # if의 인수가 1이면 결측치를 처리합니다. 결측치 처리를 하지 않으려면 if의 인수를 0으로 수정하세요. 
            # df.interpolate(method='linear' or 'polynomial')
            # 시간에 대한 결측치 처리
            merge_df['DateTime'] = merge_df['DateTime'].interpolate(method='backfill', limit=3)
            merge_df['DateTime'] = merge_df['DateTime'].interpolate(method='pad', limit=3)

            # 빈좌석에 대한 결측치 처리, limit 값이 다름에 주의
            merge_df['remainSeatCnt'] = merge_df['remainSeatCnt'].interpolate(method='linear', limit=2, limit_direction='both')

            merge_df['endBus'] = merge_df['endBus'].interpolate(method='pad', limit=3)        
            merge_df['endBus'] = merge_df['endBus'].interpolate(method='backfill', limit=3)

            merge_df['lowPlate'] = merge_df['lowPlate'].interpolate(method='pad', limit=3)        
            merge_df['lowPlate'] = merge_df['lowPlate'].interpolate(method='backfill', limit=3)

            merge_df['plateType'] = merge_df['plateType'].interpolate(method='pad', limit=3)        
            merge_df['plateType'] = merge_df['plateType'].interpolate(method='backfill', limit=3)

            merge_df['routeId'] = merge_df['routeId'].interpolate(method='pad', limit=3)        
            merge_df['routeId'] = merge_df['routeId'].interpolate(method='backfill', limit=3)

        _oneDay_df[str(plateNo)+'_'+str(index)] = merge_df['DateTime']
        # display(merge_df)
        index=i
#         print(str(plateNo)+'_'+str(index))
#         display(merge_df)
#         break;
#     break;

# _oneDay_df

In [37]:
def get_full_data_index(_oneDay_df):
    '''
    함수 [get_full_data_index(df)]은 데이터프레임 안에서 결측치가 하나도 없는 행의 index를 반환합니다.
    시간표를 배차 시간순으로 정렬하기 위해 데이터프레임의 첫번째 행을 기준으로 열(axis=1)을 정렬합니다.
    하지만 데이터프레임의 첫번째 행을 기준으로 정렬을 하게되면 결측치로 인하여 정렬이 안되는 열이 발생합니다.
    결측치가 없는 행을 찾기 위해 제작한 함수 입니다.

    '''
    for i in range(len(_oneDay_df.columns)):
        for j in range(len(_oneDay_df)):
            if(_oneDay_df.iloc[j].isnull().sum() == i):
                return j
            
        print("모든 행에 결측치가 존재합니다.")

In [112]:
# 출차시간(1행)을 기준으로 column을 정렬합니다. X > 결측치가 없는 행중 인덱스가 가장 작은 행
# oneDay_df = _oneDay_df.sort_values(by=1, axis=1)
lineIndex = get_full_data_index(_oneDay_df)+1
oneDay_df = _oneDay_df.sort_values(by=lineIndex, axis=1)


# datetime 객체를 string 객체로 변환합니다. 시간을 가지고 계산해야 하는 일은 이전에 실행하세요.
oneDayString_df = oneDay_df.astype('string')
for column in oneDayString_df.columns:
    oneDayString_df[column] = oneDayString_df[column].str.slice(start=10, stop=16)

# [column명 : 차량번호] station_df 와 oneDay_df를 합칩니다. datetime이 아닌 다른 타입의 오브젝트가 행에 붙게 되므로 지금부터는 편집이 어렵습니다.
_finalOneDay_df = pd.concat([station_df,oneDayString_df], axis=1)
_finalOneDay_df.set_index('stationSeq', drop=True, inplace=True)
# _finalOneDay_df

In [114]:
# 정렬된 column에 출차 순서를 배정합니다. (1호차, 2호차, ...)
columnCount = len(oneDayString_df.columns)
oneDayString_df.columns = np.arange(1,columnCount+1)

# [column명 : n호차] station_df 와 oneDay_df를 합칩니다. datetime이 아닌 다른 타입의 오브젝트가 행에 붙게 되므로 지금부터는 편집이 어렵습니다.
finalOneDay_df = pd.concat([station_df,oneDayString_df], axis=1)
df = finalOneDay_df.set_index('stationSeq', drop=True)
# df

## 일일 시간표 데이터 csv로 내보내기

In [113]:
_finalOneDay_df.to_csv(outputPath, encoding='utf-8-sig')

In [15]:
rootPath = 'C:/Users/jongh/OneDrive/School/석사/1-2/자료구조/프로젝트/5.DATA/Master/dataAPI/DailyTimeTable/' + str(routeId)
createFolder(rootPath)
outputPath = rootPath + '/' + str(routeId) + '_' + str(year)[-2:] + '-' + str(month) + '-' + str(day) + '.csv'
df.to_csv(outputPath, encoding='ANSI')

# CSV 파일을 읽어서 EXCEL파일로 내보낸다 : 블로그 게시 목적

## 일일 시간표 데이터 csv 읽어오기

In [16]:
df = pd.read_csv(outputPath, encoding='ANSI')

## 노선번호 받아오기

In [17]:
KEY = 'yEaR%2F3MDedRSlVJL%2F2pxnVg0yre1N5VF3RZ%2FUAt56MJ7J2mNpfqhUvy05pXV0uhHTVY7DbyCR8xmMaDdYga67Q%3D%3D' # 종현
apiKey = unquote(KEY)

# 노선정보항목조회 busrouteservice/info
# 해당 노선에 대한 노선번호, 기점/종점 정류소, 첫차/막차시간, 배차간격, 운행업체 등의 운행계획 정보를 제공합니다.
url = 'http://openapi.gbis.go.kr/ws/rest/busrouteservice/info'
queryParams = '?' + urlencode({ quote_plus('serviceKey') : apiKey, quote_plus('routeId') : routeId })
# print(url+queryParams)

request = Request(url + queryParams)
request.get_method = lambda: 'GET'
oneLineXML = urlopen(request).read().decode('utf8')
# print(oneLineXML)

xtree = ET.fromstring(oneLineXML)
resultCode = int(xtree[1].find("resultCode").text)
msgBody = xtree[2]

busRouteInfoItem = msgBody[0]
i=0
for info in busRouteInfoItem:
    print(f"{i} {info.tag} : {info.text}")
    i+=1

0 companyId : 4103400
1 companyName : 신일여객
2 companyTel : 031-958-0135
3 districtCd : 2
4 downFirstTime : 06:20
5 downLastTime : 02:20
6 endStationId : 101000022
7 endStationName : 숭례문
8 peekAlloc : 105
9 regionName : 고양,서울,파주
10 routeId : 229000263
11 routeName : 9709
12 routeTypeCd : 11
13 routeTypeName : 직행좌석형시내버스
14 startMobileNo : 30095
15 startStationId : 229000746
16 startStationName : 장터고개.맥금동영업소
17 upFirstTime : 04:50
18 upLastTime : 00:50
19 nPeekAlloc : 0


In [18]:
routeName = busRouteInfoItem.find("routeName").text

## Excel로 내보내기

In [19]:
rootPath = 'C:/Users/jongh/OneDrive/School/석사/1-2/자료구조/프로젝트/5.DATA/Master/dataAPI/ExcelExport/'
excelFileName = str(routeName) + '.xlsx'
filePath = rootPath + excelFileName

createFolder(rootPath)
print(filePath)

C:/Users/jongh/OneDrive/School/석사/1-2/자료구조/프로젝트/5.DATA/Master/dataAPI/ExcelExport/9709.xlsx


### 배포용 DataFrame 수정

In [20]:
export_df = df.set_index('stationName').drop('stationId', axis=1)

### 내보내기

In [21]:
#-- write an object to an Excel sheet using pd.DataFrame.to_excel()
export_df.to_excel(filePath, # directory and file name to write
            sheet_name = '평일', 
            na_rep = 'NaN', 
            float_format = "%.2f", 
            header = True, 
            #columns = ["group", "value_1", "value_2"], # if header is False
            index = True, 
            index_label = "정류장", 
            startrow = 0, 
            startcol = 0, 
            engine = 'openpyxl', 
            freeze_panes = (1, 1)
            )

## Excel 접근하여 수정하기
https://naakjii.tistory.com/56

In [22]:
wb = openpyxl.load_workbook(filePath)
sheet = wb['평일']

In [23]:
sheet.max_column, sheet.max_row

(17, 145)

In [24]:
sheet.column_dimensions['A'].width = 14

In [25]:
for cell in sheet['A']:
    cell.alignment = openpyxl.styles.Alignment(horizontal='left', vertical='center')
#     cell.fill = openpyxl.styles.fills.PatternFill(patternType='solid', fgColor=openpyxl.styles.colors.Color(rgb='00FF00'))

In [26]:
wb.save(filePath)

In [27]:
wb.close()